# Nested merging data analysis
This notebook allows for run-accumulated merging of LD91 data. Beginning with run 95, we add additional runs with every additional merging job, until all runs from 95 to 114 are merged in the final data-set. The idea is to examine the change in the resulting metrics (e.g $CC_{1/2}$, and anomalous peak height), and show that with more frames the metrics improve. 

We begin by ensuring the cctbx environment is loaded and that we are using the correct python from our local Anaconda environment. Firstly, we must enable set up Matplotlib within the notebook environment.

In [1]:
%matplotlib inline
%env BOOST_ADAPTBX_FPE_DEFAULT=1
import matplotlib
import matplotlib.pyplot as plt
matplotlib.rcParams['figure.figsize'] = (16,10)

env: BOOST_ADAPTBX_FPE_DEFAULT=1


In [2]:
!which libtbx.python

/net/dials/raid1/mlxd/InDev/feb_sprint/build/bin/libtbx.python


To enable MPI for use with mpi4py, we must have be running an ipyparallel cluster in the background of our server. If the ipycluster environment has not yet been installed, we can use conda
```bash
conda install ipycluster
```

For this notebook on dials, we can run the following commands:

```
libtbx.ipython profile create --parallel --profile=mpi
```

The above line will create a new profile directory `$HOME/.ipython/profile_mpi` and some configuration specific files which we can modify to allow use to run MPI-enabled jobs to suit our environment. While not all steps here may be necessary for all configurations, this is currently what has given the correct mpi4py output in the rest of the notebook.

Firstly, we must modify the `c.IPClusterEngines.engine_launcher_class` and `c.IPClusterStart.controller_launcher_class` variables in `$HOME/.ipython/profile_mpi/ipcluster_config.py` around lined 127 and 178 to:
```bash
c.IPClusterEngines.engine_launcher_class = 'MPIEngineSetLauncher'
...
c.IPClusterStart.controller_launcher_class = 'MPIControllerLauncher'
```

Next, we modify the `ipcluster` command (location found with `whcih ipcluster`) to use `libtbx.python` instead of the default `ipython` environment to ensure we have the appropriate paths variables set. For ease of use, we can simply call the following command: 
```bash
sed -i "1 s~^.*$~\#\!$(which libtbx.python)~" $(which ipcluster)
```

This will set up the environment to allow MPI-enabled jobs. We can now start our `ipcluster` environment with:
```bash
ipcluster start -n <CORES> --profile=mpi --engines=MPI
```
where `<CORES>` specifies the number of back-end MPI engines (like ranks) on which to run our jobs. We may now connect our notebook to the cluster backend, and test the functionality of mpi4py. We may also enable the ability to start and stop the cluster profiles within the Jupyterhub environment by running the following command in the terminal:
```bash
ipcluster nbextension enable --user
```
This will enable the IPythonClusters tab, and allow us to specify the number of cores and/or profiles to start.

We must ensure the mpi4py module is built with and run with the same MPI library. The shell environment that enables the Jupyter notebook and the ipycluster backend should allow for mpi4py scripts to run. As a test, ensure that the following code can run in the terminal environment:

```python
from mpi4py import MPI

size = MPI.COMM_WORLD.Get_size()
rank = MPI.COMM_WORLD.Get_rank()
name = MPI.Get_processor_name()

print "Rank %d of %d [%s]."%(rank, size, name)
```
using `mpirun -n 4 libtbx.python mpi_test.py`. If the output shows 4 ranks, next run the following command in the notebook, and the output should be identical (though different order of ranks is possible).

In [3]:
!mpirun -n 4 libtbx.python ./mpi_test.py

Rank 2 of 4 [dials.lbl.gov].
Rank 0 of 4 [dials.lbl.gov].
Rank 1 of 4 [dials.lbl.gov].
Rank 3 of 4 [dials.lbl.gov].


Now, we can tie the MPI backend into the notebook to allow us to call jobs on the cluster backend 

In [4]:
from ipyparallel import Client
c = Client(profile='mpi')

def mpi_test():
    from mpi4py import MPI
    print MPI.COMM_WORLD.size

    size = MPI.COMM_WORLD.Get_size()
    rank = MPI.COMM_WORLD.Get_rank()
    name = MPI.Get_processor_name()    

    return (rank, size, name)
c.ids
rc=c[:]
rc.apply_sync(mpi_test)

[(3, 4, 'dials.lbl.gov'),
 (0, 4, 'dials.lbl.gov'),
 (2, 4, 'dials.lbl.gov'),
 (1, 4, 'dials.lbl.gov')]

We can also make the calls asynchronous, which returns control to the notebook immediately. The results can then be fecthed once the background jobs are finished.

In [5]:
ar=rc.apply_async(mpi_test)
while not ar.ready():
    pass
for r in ar.result():
    print r

(3, 4, 'dials.lbl.gov')
(0, 4, 'dials.lbl.gov')
(2, 4, 'dials.lbl.gov')
(1, 4, 'dials.lbl.gov')


We now attempt to import a cctbx module and run a command using this, to ensure our environment is correctly configured. We import the Flex module, create a flex.double array from a python list of floats, then convert back to a list and print the values. If this succeeds, our environment is configured correctly.

In [6]:
from scitbx.array_family import flex
print list(flex.double([1.0,2.0,3.0]))

[1.0, 2.0, 3.0]


We start with defining the location of our desired directories:
- RESULTDIR is the base directory for all our analysis
- OUTDIR is where the scripts and different merge directory will live
- {OUTDIR}/subsel is for storing temporary directories for holding softlinks to the TAR files to merge
- TARDIR is the location of all TAR files
- PHENIXDIR is the location of the Phenix installation
- EXAFELDIR is the location of the exafel_project repo.

In [7]:
RESULTDIR="/net/dials/raid1/mlxd/InDev/feb_sprint/"
OUTDIR=RESULTDIR+'/nested_merging2'
%mkdir -p {OUTDIR}/subsel
%cd {OUTDIR}
TARDIR='/net/dials/raid1/mlxd/TAR/'
PHENIXDIR="/net/cci/mlxd/ml/builds/sept_sprint/myDir/phenix"
EXAFELDIR="/net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging/exafel_project"

/net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2


Next, we take a count of the total number of cores on the system, and set the scripts to use this amount of MPI-ranks when merging. 

In [8]:
import multiprocessing as mp
cores = mp.cpu_count()//2
print "Using %d cores"%cores

Using 32 cores


To best allow for the MPI-enabled process to run, we can examine two methods: 
1. Using shell scripts to generate the required files and merge commands which are called from the notebook 
2. Running the MPI-enabled work entirely from within the notebook.

We will examine option 1. initially, and see if this fits out needs.

Firstly, we create the command-scripts to compute the nested merge jobs. We can begin with a templated file with sections to replace with the desired values for each merge job. We create a bash array which maintains a list of all the files matching the specific TAR run numbers required for the merge (eg [95], [95,96], [95,96,97], etc.). We then patch the submission script, replacing the `<templated>` regions with the required values.

In [9]:
MERGE='''
cd <OUTDIR>;

TMPDIR=$(mktemp -d);
if [ -z "${TMPDIR}" ]
then
  echo 'Failed to create temporary directory. Exiting.';
  exit -1;
fi

DATADIR=<OUTDIR>/subsel/$(basename ${TMPDIR});
ln -sf ${TMPDIR} ${DATADIR};
for ii in $(ls <TARDIR>/<glob_template>);
do
  ln -sf ${ii} ${DATADIR}
done;
#trap "{ rm -rf ${TMPDIR}; rm <OUTDIR>/subsel/$(basename ${TMPDIR}); }" ERR
export TARDATA=${DATADIR}/*.tar;
cp /net/dials/raid1/mlxd/InDev/test/refModel/4ngz* <OUTDIR>;
export MERGE_ROOT=<OUTDIR>;
export TAG=1n_merge_<tag_template>;
export MULTINODE=True;
mkdir -p ${MERGE_ROOT}/${TAG};

source ${CONDA_PREFIX}/../../bin/activate myEnv
echo "START RANK=0 TIME=" $(date +%s);
mpirun -np <CORES> <EXAFELDIR>/137-nested_merge/merge_local.sh;
echo "STOP RANK=0 TIME=" $(date +%s);

export EXAFEL_DIR=<EXAFELDIR>
export PHENIX_ROOT=<PHENIXDIR>
export MULTINODE=False;
<EXAFELDIR>/137-nested_merge/merge_local.sh;
'''
MERGE = MERGE.replace('<OUTDIR>',OUTDIR)\
.replace('<TARDIR>',TARDIR)\
.replace('<CORES>', str(cores))\
.replace('<PHENIXDIR>', PHENIXDIR)\
.replace('<EXAFELDIR>',EXAFELDIR)
MERGE_FILE = open("MERGE_FILE.sh", "w")
MERGE_FILE.write(MERGE)
MERGE_FILE.close()

The above file explicitly sets up directories containing softlinks to the files for each nested merge step, and runs these using the specified commands in `exafel_project/137-nested_merge/merge_local.sh`. The resulting directory containing the softlinks is removed upon exit of the script. We now generate the templated files for each merging job, and subsequently run these providing the location of the `<OUTDIR>` and the `<exafel_project>` directory as arguments.

In [10]:
%%bash
shopt -s extglob
export TARDIR=$TARDIR #Pass in the directory with the tar files:   eg  /my/scratch/dir/TAR_95-114
export OUTDIR=$OUTDIR #Pass in the directory for burst-buffer data to be staged out:   /my/scratch/dir/bb_out
RUNARRAY=() #Array to hold the structure of the files to be processed

#Iterate over the given runs and generate the TAR globs
echo "Generating expanded globs for TAR file paths"
for ii in $(seq -w 95 114); do
  RUNARRAY+=($ii)
  str=""
  for jj in ${RUNARRAY[@]}; do
    str+=$jj,
  done
  str=$(echo $str | sed s'/.$//')
  if [ "${#RUNARRAY[@]}" == "1" ]; then
    g=$(eval "echo \"r0${str}*.tar\" ")
  else
    g=$(eval "echo \"r0{${str}}*.tar\" ") 
  fi  
  echo $g
  
  #Create a submission script with the appropriate arguments
  cat ./MERGE_FILE.sh | sed "s~<tag_template>~r0${ii}~g; s~<glob_template>~${g}~g; s~<tar_template>~${TARDIR}~g; s~<data_out_template>~${OUTDIR}~g" > merge_r0${ii}.sh
  chmod +x merge_r0${ii}.sh
done

Generating expanded globs for TAR file paths
r0095*.tar
r0{095,096}*.tar
r0{095,096,097}*.tar
r0{095,096,097,098}*.tar
r0{095,096,097,098,099}*.tar
r0{095,096,097,098,099,100}*.tar
r0{095,096,097,098,099,100,101}*.tar
r0{095,096,097,098,099,100,101,102}*.tar
r0{095,096,097,098,099,100,101,102,103}*.tar
r0{095,096,097,098,099,100,101,102,103,104}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110,111}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110,111,112}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110,111,112,113}*.tar
r0{095,096,097,098,099,100

To run the merge job for run95 using the generated bash scripts, we run the following command.

In [11]:
! ./merge_r0095.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/

START RANK=0 TIME= 1520975056
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.UQ2ocJ0XRj/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0095 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scaling.mtz_file=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz scaling.mtz_column_F=f(+) min_corr=-1.0 unit_cell_length_tolerance=0.0065 raw_data.errors_from_sample_residuals=False raw_data.sdfac_refine=True raw_data.error_models.sdfac_refine.random_seed=42 cell_rejection.unit_cell=78.95,78.95,38.12,90.0,90.0,90.0 cell_rejection.space_group=P43212 output.prefix=1n_merge_r0095
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.UQ2ocJ0XRj/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0095 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=T

The following parameters have been modified:

targlob = "/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.UQ2ocJ0XRj/*.tar"
model = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb
d_min = 2.0
pixel_size = 0.11
min_corr = -1.0
unit_cell_length_tolerance = 0.0065
nproc = 1
raw_data {
  sdfac_refine = True
  error_models {
    sdfac_refine {
      random_seed = 42
    }
  }
}
output {
  prefix = 1n_merge_r0095
}
scaling {
  mtz_file = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz
  mtz_column_F = f(+)
  report_ML = True
}
postrefinement {
  enable = True
}
cell_rejection {
  unit_cell = 78.95,78.95,38.12,90.0,90.0,90.0
  space_group = P43212
}
backend = *FS MySQL SQLite Flex
mysql {
  runtag = 1n_merge_r0095
}

I model
Number of scatterers: 1164
At special positions: 0
Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
Space group: P 43 21 2 (No. 96)
Miller array info: None
Observation type: None
Type of data: double, size=15080
Type of s

--------------------------------------------------------------------------------
Step 2.  Load pickle file into dictionary obj and filter on lattice & cell with h,k,l
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.UQ2ocJ0XRj/r0095_int-0-0119.pickle.tar;member00000;timestampint-0-20140615213937601.pickle

P 4/m m m
(79.1611, 79.1611, 38.215, 90, 90, 90)
Integrated data:
  Miller array info: None
  Observation type: xray.intensity
  Type of data: double, size=71
  Type of sigmas: double, size=71
  Number of Miller indices: 71
  Anomalous flag: None
  Unit cell: (79.1611, 79.1611, 38.215, 90, 90, 90)
  Space group: P 4/m m m (No. 123)
mean diff is 0.220158918112 range 0.0055394188898 0.462415218612
Step 3. Correct for polarization.
Step 4. Filter on global resolution and map to asu
Data in reference setting:

 Bin  Resolution Range  Compl.         <I>     <I/sig(I)>
   1 16.9468 -  4.0997 [14/1718]      1067.9      22.9
   2  4.0997 -  3.2616 [10/1710]      1623.6     

--------------------------------------------------------------------------------
Step 2.  Load pickle file into dictionary obj and filter on lattice & cell with h,k,l
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.UQ2ocJ0XRj/r0095_int-0-0024.pickle.tar;member00000;timestampint-0-20140615213916263.pickle

P 4/m m m
(79.3056, 79.3056, 38.2109, 90, 90, 90)
Integrated data:
  Miller array info: None
  Observation type: xray.intensity
  Type of data: double, size=81
  Type of sigmas: double, size=81
  Number of Miller indices: 81
  Anomalous flag: None
  Unit cell: (79.3056, 79.3056, 38.2109, 90, 90, 90)
  Space group: P 4/m m m (No. 123)
mean diff is 0.185729802524 range 0.00406804464032 0.451615607558
Step 3. Correct for polarization.
Step 4. Filter on global resolution and map to asu
Data in reference setting:

 Bin  Resolution Range  Compl.         <I>     <I/sig(I)>
   1 19.6483 -  4.2928 [23/1508]      2326.2      32.8
   2  4.2928 -  3.4131 [ 6/1493]      1432.2  

--------------------------------------------------------------------------------
Step 2.  Load pickle file into dictionary obj and filter on lattice & cell with h,k,l
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.UQ2ocJ0XRj/r0095_int-0-0125.pickle.tar;member00000;timestampint-0-20140615213921731.pickle

P 4/m m m
(79.1505, 79.1505, 38.111, 90, 90, 90)
Integrated data:
  Miller array info: None
  Observation type: xray.intensity
  Type of data: double, size=85
  Type of sigmas: double, size=85
  Number of Miller indices: 85
  Anomalous flag: None
  Unit cell: (79.1505, 79.1505, 38.111, 90, 90, 90)
  Space group: P 4/m m m (No. 123)
mean diff is 0.193126563362 range 0.0123141655995 0.414124671947
Step 3. Correct for polarization.
Step 4. Filter on global resolution and map to asu
Data in reference setting:

 Bin  Resolution Range  Compl.         <I>     <I/sig(I)>
   1 11.8440 -  4.0534 [19/1732]      5360.7      58.4
   2  4.0534 -  3.2390 [14/1733]      8275.4     

...

48.08 52.67   4.60  0.002   0.4    0.0   0.0   0.0    0  0.125  6.302  0.0093
47.29 52.40   5.11  0.004   0.5    0.5   0.0   0.0    0  0.250  6.285  0.0109
46.13 52.33   6.20  0.006   0.7    2.5   0.0   0.0    0  0.500  6.258  0.0168
44.99 52.57   7.59  0.009   1.1    6.1   0.0   0.0    0  1.000  6.233  0.0274
43.44 53.48  10.04  0.013   1.6   14.8   0.8   0.0    0  2.000  6.198  0.0524
42.83 54.13  11.30  0.018   2.0   24.5   3.1   0.0    0  3.000  6.176  0.0799
42.27 54.33  12.06  0.022   2.3   33.6   3.1   1.9    0  4.000  6.156  0.1099
41.80 54.31  12.52  0.026   2.5   40.2   3.1   1.9    0  5.000  6.142  0.1284
41.36 54.34  12.99  0.031   2.8   42.3   3.1   2.9    0  6.000  6.130  0.1560
41.05 54.51  13.46  0.033   3.1   50.9   3.1   2.9    1  7.000  6.119  0.2004
40.81 54.56  13.75  0.036   3.3   57.1   3.1   4.8    3  8.000  6.108  0.2148
40.49 55.03  14.55  0.040   3.5   60.6   3.1   4.8    4  9.000  6.099  0.2487
40.30 55.17  14.87  0.043   3.7   61.1   4.7   5.7    5 10.000  


                         ----------X-ray data----------                        

|--(resolution: 2.00 - 25.49 A, n_refl.=2152 (all), 7.62  % free)-------------|
|                                                                             |
| r_work= 0.4819 r_free= 0.5269 coordinate error (max.-lik. estimate): 0.61 A |
|                                                                             |
| normalized target function (ml) (work): 6.302844                            |
| target function (ml) not normalized (work): 12530.054376                    |
| target function (ml) not normalized (free): 1024.547602                     |
|-----------------------------------------------------------------------------|

|-----------------------------------------------------------------------------|
| Bin     Resolution   Compl.  No. Refl.    R-factors          Targets        |
|number     range              work test   work   test        work        test|
|  1: 25.4898 -  2.0007 0.14   1988  


============================== Collecting inputs ==============================


                   ----------Processing X-ray data----------                   

I-obs:
  /net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2/1n_merge_r0095/1n_merge_r0095.mtz:Iobs(+),SIGIobs(+),Iobs(-),SIGIobs(-)
Miller array info: /net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2/1n_merge_r0095/1n_merge_r0095.mtz:Iobs(+),SIGIobs(+),Iobs(-),SIGIobs(-)
Observation type: xray.intensity
Type of data: double, size=2295
Type of sigmas: double, size=2295
Number of Miller indices: 2295
Anomalous flag: True
Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
Space group: P 43 21 2 (No. 96)
Systematic absences: 0
Centric reflections: 278
Resolution range: 25.4878 2.00067
Completeness in resolution range: 0.153337
Completeness with d_max=infinity: 0.153266
Anomalous completeness in resolution range: 0.0269626
Bijvoet pairs: 181
Lone Bijvoet mates: 1655
Mean anomalous difference: 0.7760
Wavelength: 1.3853


  

(-11, -2, -16)    63461.477      334110.438    30171.216
(-32, -9, -6)    132993.422      1071457.625    31614.456
(37, 4, 0)    52837.633      972054.688    21804.937
(-35, -3, -6)    16263.574      169479.188    20940.654
(-36, -3, -3)    72280.094      914388.438    24700.954
(32, 15, 7)    23470.793      436097.500    21751.396
(-16, -1, -16)    18770.402      129551.742    19834.648
(-29, -16, -9)    10105.749      197811.391    20817.468
-----------------------------------------------------------------
Intensities converted to amplitudes for use in refinement.

Number of F-obs in resolution range:                   2171
Number of F-obs<0 (these reflections will be rejected): 0
Number of F-obs=0 (these reflections will be used in refinement): 0
Refinement resolution range: d_max =  25.4878
                             d_min =   2.0007


Fobs statistics after all cutoffs applied:

Miller array info: None
Observation type: xray.amplitude
Type of data: double, size=2014
Type of sigma

      100.55 -   107.24: 49
      107.24 -   113.92: 2210
      113.92 -   120.60: 709
      120.60 -   127.28: 565
      127.28 -   133.97: 15
  Bond angle restraints: 3548
  Sorted by residual:
  angle pdb=" CA  SER A  36 "
        pdb=" C   SER A  36 "
        pdb=" N   ASN A  37 "
      ideal   model   delta    sigma   weight residual
     116.20  119.47   -3.27 2.00e+00 2.50e-01 2.67e+00
  angle pdb=" CA  ARG A 114 "
        pdb=" C   ARG A 114 "
        pdb=" N   CYS A 115 "
      ideal   model   delta    sigma   weight residual
     116.20  119.28   -3.08 2.00e+00 2.50e-01 2.37e+00
  angle pdb=" CA  TRP A  63 "
        pdb=" C   TRP A  63 "
        pdb=" N   CYS A  64 "
      ideal   model   delta    sigma   weight residual
     116.20  119.19   -2.99 2.00e+00 2.50e-01 2.23e+00
  angle pdb=" CA  ARG A  68 "
        pdb=" C   ARG A  68 "
        pdb=" N   THR A  69 "
      ideal   model   delta    sigma   weight residual
     116.20  119.09   -2.89 2.00e+00 2.50e-01 2.09e+00
  an

We can now parse the output directory for information on the resulting merge job. In this instance, we simply look for the number of frames used, and the resulting anomalous peak height value. Though, we can opt to look for additional parameters quite easily.

In [15]:
%%bash
for ii in $(find $PWD -type f -iname "1n_merge_*95.log" | grep -v mark0 | grep -v graphs | grep -v peak | grep -v 001);
do
  echo $(basename $ii);
  sed '9q;d' $ii;
done
for ii in $(find $PWD -type f -iname "*peak*log" | grep 0095);
do
  echo $(basename $ii)
  str=$(tail -n 1 $ii)
  if [[ "$str" = *"sigma"* ]]; then
      echo $str
  else
      echo "Unable to calculate anom. peak height."
  fi
done

1n_merge_r0095.log
  38 of 38 integration files were accepted
1n_merge_r0095.log
  38 of 38 integration files were accepted
1n_merge_r0095_peakht.log
Unable to calculate anom. peak height.
1n_merge_r0095_peakht.log
Unable to calculate anom. peak height.


As we can see, using very little data gives us a poor result for the anom. peak height (in this case, no result). We can run one of the other nested merge scripts with more data to allow us to acquire a result. We begin by adding in runs 96 and 97 to the job using:

In [16]:
! ./merge_r0097.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/

START RANK=0 TIME= 1520975910
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0097 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scaling.mtz_file=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz scaling.mtz_column_F=f(+) min_corr=-1.0 unit_cell_length_tolerance=0.0065 raw_data.errors_from_sample_residuals=False raw_data.sdfac_refine=True raw_data.error_models.sdfac_refine.random_seed=42 cell_rejection.unit_cell=78.95,78.95,38.12,90.0,90.0,90.0 cell_rejection.space_group=P43212 output.prefix=1n_merge_r0097
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0097 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=T

The following parameters have been modified:

targlob = "/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/*.tar"
model = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb
d_min = 2.0
pixel_size = 0.11
min_corr = -1.0
unit_cell_length_tolerance = 0.0065
nproc = 1
raw_data {
  sdfac_refine = True
  error_models {
    sdfac_refine {
      random_seed = 42
    }
  }
}
output {
  prefix = 1n_merge_r0097
}
scaling {
  mtz_file = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz
  mtz_column_F = f(+)
  report_ML = True
}
postrefinement {
  enable = True
}
cell_rejection {
  unit_cell = 78.95,78.95,38.12,90.0,90.0,90.0
  space_group = P43212
}
backend = *FS MySQL SQLite Flex
mysql {
  runtag = 1n_merge_r0097
}

I model
Number of scatterers: 1164
At special positions: 0
Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
Space group: P 43 21 2 (No. 96)
Miller array info: None
Observation type: None
Type of data: double, size=15080
Type of s

/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0059.pickle.tar 3
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0060.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0062.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0065.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0066.pickle.tar 3
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0068.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0069.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0070.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0071.pickle.tar 2
/net/dials/raid1/mlxd/InDev/

/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0218.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0219.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0220.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0221.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0224.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0225.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0228.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0229.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0232.pickle.tar 1
/net/dials/raid1/mlxd/InDev/

/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0402.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0406.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0407.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0408.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0412.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0413.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0414.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0415.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.6knZWMYZHD/r0096_int-0-0417.pickle.tar 1
/net/dials/raid1/mlxd/InDev/

...

  number           = 39     
  b_iso_min        = 8.51    (limit = 1.00)
  b_iso_max        = 38.43   (limit = 80.00)
  b_iso_mean       = 20.08               
  anisotropy_min   = 1.00    (limit = 0.10)
  occupancy_min    = 1.00    (limit = 0.10)
  occupancy_max    = 1.00    (limit = 1.00)
  dist_sol_mol_min = 2.02    (limit = 1.80)
  dist_sol_mol_max = 4.69    (limit = 6.00)

                         ----------X-ray data----------                        

|--(resolution: 2.00 - 27.79 A, n_refl.=11553 (all), 8.18  % free)------------|
|                                                                             |
| r_work= 0.3539 r_free= 0.3723 coordinate error (max.-lik. estimate): 0.50 A |
|                                                                             |
| normalized target function (ml) (work): 5.986454                            |
| target function (ml) not normalized (work): 63504.303506                    |
| target function (ml) not normalized (free): 5702.899201 

Writing refined structure to PDB file:
  /net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2/1n_merge_r0097/1n_merge_r0097_001.pdb
n_use            =  2002
n_use_u_iso      =  2001
n_use_u_aniso    =  1
n_grad_site      =  0
n_grad_u_iso     =  0
n_grad_u_aniso   =  0
n_grad_occupancy =  0
n_grad_fp        =  0
n_grad_fdp       =  0
total number of scatterers =  2002

Writing default parameters for subsequent refinement:
  /net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2/1n_merge_r0097/1n_merge_r0097_002.def


=============================== Detailed timings ==============================

  Micro-tasks:
    mask                            = 0.00   
    f_calc                          = 0.00   
    alpha_beta                      = 1.15   
    target                          = 0.32   
    gradients_wrt_atomic_parameters = 0.00   
    fmodel                         = 0.00   
    r_factors                      = 0.02   
    phase_errors                   = 2.04   
    foms      

(-25, -1, -13)    393092.500      255948.641    41318.132
(-18, -14, -14)    98581.039      215467.297    37843.229
(-31, -21, -2)    188535.734      243853.062    32370.944
(31, 20, 5)    141234.688      249080.938    39586.660
(36, 11, 3)    236280.938      280021.625    35766.615
(-22, -18, -12)    60958.312      168041.828    35535.059
(29, 19, 8)    465427.781      419138.375    34987.637
(34, 16, 4)    155297.438      223555.609    39009.994
(21, 8, 15)    245927.266      312948.062    35865.699
(-12, -9, -17)    73457.961      165924.203    34951.256
(38, 9, 1)    176574.484      214779.000    34748.919
-----------------------------------------------------------------
Intensities converted to amplitudes for use in refinement.

Number of F-obs in resolution range:                   11580
Number of F-obs<0 (these reflections will be rejected): 0
Number of F-obs=0 (these reflections will be used in refinement): 0
Refinement resolution range: d_max =  27.7854
                       

    ideal  model  delta    sigma   weight residual
    1.451  1.438  0.013 1.60e-02 3.91e+03 6.74e-01
  bond pdb=" C   ASP A  87 "
       pdb=" N   ILE A  88 "
    ideal  model  delta    sigma   weight residual
    1.329  1.340 -0.011 1.40e-02 5.10e+03 6.22e-01
  bond pdb=" C   ILE A  78 "
       pdb=" N   PRO A  79 "
    ideal  model  delta    sigma   weight residual
    1.341  1.329  0.012 1.60e-02 3.91e+03 5.40e-01
  ... (remaining 1979 not shown)

  Histogram of bond angle deviations from ideal:
      100.10 -   106.90: 30
      106.90 -   113.69: 2216
      113.69 -   120.48: 692
      120.48 -   127.27: 595
      127.27 -   134.06: 15
  Bond angle restraints: 3548
  Sorted by residual:
  angle pdb=" C   ILE A  88 "
        pdb=" CA  ILE A  88 "
        pdb=" CB  ILE A  88 "
      ideal   model   delta    sigma   weight residual
     111.60  107.05    4.55 2.00e+00 2.50e-01 5.19e+00
  angle pdb=" C   ASN A  37 "
        pdb=" N   PHE A  38 "
        pdb=" CA  PHE A  38 "
      ide

['CRYST1', '78.589', '78.589', '37.017', '90.00', '90.00', '90.00', 'P', '43', '21', '2']
['REMARK', '3', '7', '2.1059', '-', '2.0005', '0.46', '895', '75', '0.4088', '0.4431', '0.459', '0.197']


In [19]:
%%bash
for ii in $(find $PWD -type f -iname "1n_merge_*9[57].log" | grep -v mark0 | grep -v graphs | grep -v peak | grep -v 001);
do
  echo $(basename $ii);
  sed '9q;d' $ii;
done
for ii in $(find $PWD -type f -iname "*9[57]*peak*log");
do
  echo $(basename $ii)
  str=$(tail -n 1 $ii)
  if [[ "$str" = *"sigma"* ]]; then
      echo $str
  else
      echo "Unable to calculate anom. peak height."
  fi
done

1n_merge_r0095.log
  38 of 38 integration files were accepted
1n_merge_r0097.log
  433 of 750 integration files were accepted
1n_merge_r0095.log
  38 of 38 integration files were accepted
1n_merge_r0095_peakht.log
Unable to calculate anom. peak height.
1n_merge_r0097_peakht.log
pdb="YB YB A 203 " : 1.73 sigma
1n_merge_r0095_peakht.log
Unable to calculate anom. peak height.


We now have enough data for a value to be calculated (albeit a very small one). Performing the merging with higher runs will allow the number to increase even further. Using this method we are running the merging jobs interactively. It may make more sense to run the jobs asynchronously using the IPyCluster backend we mentioned earlier. This way, we get an immediate return from the job submission, and can easily work in the notebook wihile the jobs are running in the background. 

Otherwise, we can simply call the previous submission script using the entire data set. As this job may take a long time, it may be worth sending the calling process into the background, so that we may manipulate other cells in the notebook. This can also help alleviate issues where the stdout cannot reach the notebook momentarily and causes write failures (potentially).


In [48]:
%%script bash --bg 
./merge_r0099.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/ &> ./background_output_99.log
    
./merge_r0104.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/ &> ./background_output_104.log
    
./merge_r0109.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/ &> ./background_output_109.log
    
./merge_r0114.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/ &> ./background_output_114.log
    

Starting job # 3 in a separate thread.


In [21]:
!tail ./background_output_99.log

  RMS(bonds)            =   0.0020
  RMS(angles)           =   0.44
  Resolution            =   2.00
  R-work                =   0.3115
  R-free                =   0.3257
  Refinement program    = PHENIX

Results written to 1n_merge_r0099_molprobity.out
['CRYST1', '78.589', '78.589', '37.017', '90.00', '90.00', '90.00', 'P', '43', '21', '2']
['REMARK', '3', '8', '2.0915', '-', '2.0005', '0.60', '1045', '100', '0.3624', '0.3613', '0.434', '0.229']


Now we would like to view the results of the merging job. We can use Pandas' DataFrame object to display the resulting table data. Here we will examine the nested merge output using all data (runs 95 to 114).

In [22]:
from exafel_project.mlxd.utils import pd_table as pdt
tb_0095 = pdt.pd_table(OUTDIR,'1n_merge_r0095')
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

['CRYST1', '78.589', '78.589', '37.017', '90.00', '90.00', '90.00', 'P', '43', '21', '2']
['REMARK', '3', '1', '25.4898', '-', '2.0007', '0.14', '1988', '164', '0.4819', '0.5269', '0.613', '0.510']


Jupyter notebooks nicely format pandas DataFrame objects, so we can view the resulting tables 1 and 2 in their own cells. Note: To plot any of the data, we must force convert the columns to numeric data types. We cannot do the entire table 1 as some fields are not strictly numbers. Table 2 though allows us to do this.

In [23]:
tb_0095.t1.transpose()

0
Anomalous peak height                    NaN
Bond angles                            0.421
Bond lengths                           0.002
CC*                                      N/A
CC1/2                              0.0 (0.0)
CCano                                    N/A
CCiso                           27.0 (-19.4)
Clashscore                                 0
Completeness                      15.3 (4.5)
Favored                                96.85
I/sigI                             5.0 (2.0)
Ligand/ion                                 3
Multiplicity (Stills)              0.2 (0.1)
No. collected images                     N/A
No. images used                           38
No. lattices merged                       38
No. total reflections              2295 (68)
Outliers                                   0
Protein                                 1001
Resolution             25.5-2.00 (2.07-2.00)
Rsplit                           105.4 (nan)
Rwork / Rfree          48.2/52.7 (48.2/52.7)
Space group                        P 43 21 2
Water                                      5
Wilson B factor                        19.33
a                               79.18+/-0.11
alpha                                     90
b                               79.18+/-0.11
beta                                      90
c                               38.16+/-0.06
gamma                                     90

In [24]:
tb_0095.t2 = tb_0095.t2.astype(float)
tb_0095.t2

<I/sigI>  <Multiplicity>  CC1/2  CCiso  Completeness  No. Lattices  \
0     7.275            0.43   -6.7   14.2         33.89          38.0   
1     8.240            0.26   19.1   30.7         23.11          38.0   
2     5.556            0.22    8.5   19.6         20.00          37.0   
3     3.976            0.17   10.4    6.8         15.65          37.0   
4     3.472            0.16   12.4    2.7         14.25          37.0   
5     2.750            0.15   14.2   -2.2         13.58          34.0   
6     2.446            0.13   34.4    0.0         12.04          35.0   
7     2.717            0.10   -8.7   -1.6          9.23          31.0   
8     1.764            0.07   84.8    3.0          6.85          31.0   
9     2.018            0.05    0.0  -19.4          4.51          29.0   

   No. Measurements  No. Unique reflections  Resolution High  Resolution Low  \
0             654.0                   511.0             4.31             inf   
1             391.0                   345.0             3.42        4.310000   
2             326.0                   299.0             2.99        3.420000   
3             260.0                   235.0             2.71        2.990000   
4             233.0                   214.0             2.52        2.710000   
5             218.0                   203.0             2.37        2.520000   
6             195.0                   179.0             2.25        2.370000   
7             145.0                   140.0             2.15        2.250000   
8             107.0                   101.0             2.07        2.150000   
9              71.0                    68.0             2.00        2.070000   

   Rsplit  
0   110.3  
1   100.6  
2    99.0  
3    80.3  
4    52.8  
5    85.9  
6    57.4  
7    97.2  
8    42.0  
9     NaN

In [ ]:
tb_0095.t2.plot(y='<I/sigI>',x='Resolution High', linestyle='-', linewidth=0.8, c='k', alpha=0.8, fontsize=16)

##################################

[TBC - These cells are in development, and may fail outright] 

We can call the `dev_cluster_two_merge.py` script by first importing it and then providing the Phil params within the notebook (non-shell) environment. 

In [111]:
effective_params="d_min=2.0 \
targlob=\"${TARDATA}\" \
model=${MERGE_ROOT}/4ngz.pdb \
backend=FS \
mysql.runtag=${trial} \
scaling.report_ML=True \
pixel_size=0.11 \
nproc=1 \
postrefinement.enable=True \
scaling.mtz_file=${MERGE_ROOT}/4ngz.mtz \
scaling.mtz_column_F=f(+) \
min_corr=-1.0 \
unit_cell_length_tolerance=0.0065 \
raw_data.errors_from_sample_residuals=False \
raw_data.sdfac_refine=True \
raw_data.error_models.sdfac_refine.random_seed=42 \
cell_rejection.unit_cell=78.95,78.95,38.12,90,90,90 \
cell_rejection.space_group=P43212 \
output.prefix=${trial}"

In [125]:
def run_merge():
    from xfel.merging.command_line import dev_mpi_cluster_two_merge as c2m
    from mpi4py import MPI
    comm = MPI.COMM_WORLD
    rank = comm.Get_rank()

    script = c2m.Script(c2m.scaling_manager_mpi)
    result = script.run(comm=comm,timing=False)
    if rank == 0:
      script.show_plot(result)
    print "DONE"

In [114]:
c = Client(profile='mpi')
rc=c[:]

In [129]:
ar=rc.apply_async(mpi_test, effective_params)

In [133]:
ar=rc.apply_async(run_merge)
while not ar.ready():
    print ar.stdout, ar.stderr

['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', ''] ['', '', '', '']
['', '', '', '

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

...

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options] [param.phil] \n\n__main__.py: error: no such option: --profile-dir\n', '', '']
['', '', '', ''] ['', u'Usage: libtbx.ipython [options]

KeyboardInterrupt: 

In [136]:
rc.run('/net/dials/raid1/mlxd/InDev/feb_sprint/modules/cctbx_project/xfel/merging/command_line/dev_mpi_cluster_two_merge.py ' + effective_params)

IOError: [Errno 2] No such file or directory: '/net/dials/raid1/mlxd/InDev/feb_sprint/modules/cctbx_project/xfel/merging/command_line/dev_mpi_cluster_two_merge.py d_min=2.0 targlob="${TARDATA}" model=${MERGE_ROOT}/4ngz.pdb backend=FS mysql.runtag=${trial} scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scaling.mtz_file=${MERGE_ROOT}/4ngz.mtz scaling.mtz_column_F=f(+) min_corr=-1.0 unit_cell_length_tolerance=0.0065 raw_data.errors_from_sample_residuals=False raw_data.sdfac_refine=True raw_data.error_models.sdfac_refine.random_seed=42 cell_rejection.unit_cell=78.95,78.95,38.12,90,90,90 cell_rejection.space_group=P43212 output.prefix=${trial}'